```
This notebook sets up and runs a test case for analyzing Kelvin waves
Copyright (C) 2018 - 2022 SINTEF Digital
Copyright (C) 2018 - 2022 Norwegian Meteorological Institute

This program is free software: you can redistribute it and/or modify
it under the terms of the GNU General Public License as published by
the Free Software Foundation, either version 3 of the License, or
(at your option) any later version.

This program is distributed in the hope that it will be useful,
but WITHOUT ANY WARRANTY; without even the implied warranty of
MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
GNU General Public License for more details.

You should have received a copy of the GNU General Public License
along with this program.  If not, see <http://www.gnu.org/licenses/>.
```

In [1]:
import sys
gpuocean_path = [p[:-4] for p in sys.path if p.endswith("gpuocean/src")][0]
import git
repo = git.Repo(gpuocean_path)
print("GPUOcean code from:", repo.head.object.hexsha, "on branch", repo.active_branch.name)

GPUOcean code from: d92f9ec19b8873dc2feae055b1397431414ccc9e on branch reduced_gravity


# Wind
Testing wind forcing

In [2]:
#Lets have matplotlib "inline"
%matplotlib inline

import os
import sys

#Import packages we need
import numpy as np
from netCDF4 import Dataset
import datetime, copy
from IPython.display import display

#For plotting
import matplotlib
from matplotlib import pyplot as plt

plt.rcParams["lines.color"] = "w"
plt.rcParams["text.color"] = "w"
plt.rcParams["axes.labelcolor"] = "w"
plt.rcParams["xtick.color"] = "w"
plt.rcParams["ytick.color"] = "w"

plt.rcParams["image.origin"] = "lower"

In [3]:
from gpuocean.utils import IPythonMagic, NetCDFInitialization

In [4]:
%cuda_context_handler gpu_ctx

In [11]:
from IPython.display import clear_output
from matplotlib import animation, rc
plt.rcParams["animation.html"] = "jshtml"
from mpl_toolkits.axes_grid1 import make_axes_locatable

from gpuocean.utils import PlotHelper
from gpuocean.utils.NetCDFInitialization import depth_integration

def plotSolution(fig, 
                 eta, hu, hv, h, dx, dy, 
                 t, red_grav_mode=False,
                 comment = "Oslo",
                 h_min=-0.25, h_max=0.25, 
                 uv_min=-5, uv_max=5,
                 ax=None, sp=None, quiv=None):


    from datetime import timedelta
    fig.suptitle("Time = " + str(datetime.datetime.utcfromtimestamp(t).strftime('%Y-%m-%d %H:%M:%S')) + " " + comment, 
                 fontsize=18,
                 horizontalalignment='left')
    
    ny, nx = eta.shape
    domain_extent = [0, nx*dx/1000, 0, ny*dy/1000]
    
    x_plots = 4
    y_plots = 1
   
    huv_label = ["hv","hu"]

    # Prepare quiver
    u = hu/(h+eta)
    v = hv/(h+eta)
    velocity = np.sqrt(u*u + v*v)
    
    frequency_x = 10
    frequency_y = 10
    x = np.arange(0, velocity.shape[1], frequency_x)*dx
    y = np.arange(0, velocity.shape[0], frequency_y)*dy
    qu = u[::frequency_y, ::frequency_x]
    qv = v[::frequency_y, ::frequency_x]

    if red_grav_mode:
        eta = -(h+eta)
        h_min = -15
        h_max = 0

    if (ax is None):
        ax = [None]*x_plots*y_plots
        sp = [None]*x_plots*y_plots

        uv_cmap = plt.cm.coolwarm
        uv_cmap.set_bad("grey", alpha = 1.0)
        
        h_cmap = plt.cm.coolwarm
        h_cmap.set_bad("grey", alpha = 1.0)
        if red_grav_mode:
            h_cmap = plt.cm.Blues_r
            h_cmap.set_bad("grey", alpha = 1.0)

        velo_cmap = plt.cm.Reds
        velo_cmap.set_bad("grey", alpha = 1.0)

        ax[0] = plt.subplot(y_plots, x_plots, 1)
        sp[0] = ax[0].imshow(eta, interpolation="none", origin='lower', 
                             cmap=h_cmap, 
                             vmin=h_min, vmax=h_max, 
                             extent=domain_extent)
        plt.axis('image')
        plt.title("MLD")
        divider0 = make_axes_locatable(ax[0])
        cax0 = divider0.append_axes('right', size='5%', pad=0.05)
        fig.colorbar(sp[0],cax=cax0)


        ax[1] = plt.subplot(y_plots, x_plots, 2)
        sp[1] = ax[1].imshow(hu, interpolation="none", origin='lower', 
                            cmap=uv_cmap, 
                            vmin=uv_min, vmax=uv_max, 
                            extent=domain_extent)
        plt.axis('image')
        plt.title("$"+huv_label[0]+"$")
        divider1 = make_axes_locatable(ax[1])
        cax1 = divider1.append_axes('right', size='5%', pad=0.05)
        fig.colorbar(sp[1],cax=cax1)



        ax[2] = plt.subplot(y_plots, x_plots, 3)
        sp[2] = ax[2].imshow(hv, interpolation="none", origin='lower', 
                             cmap=uv_cmap, 
                             vmin=uv_min, vmax=uv_max, 
                             extent=domain_extent)
        plt.axis('image')
        plt.title("$"+huv_label[1]+"$")
        divider2 = make_axes_locatable(ax[2])
        cax2 = divider2.append_axes('right', size='5%', pad=0.05)
        fig.colorbar(sp[2],cax=cax2)

        ax[3] = plt.subplot(y_plots, x_plots, 4)
        sp[3] = ax[3].imshow(velocity, interpolation="none", origin='lower', 
                             cmap="Reds", 
                             vmin=0, vmax=1.0, 
                             extent=domain_extent)
        quiv = ax[3].quiver(x,y,qu,qv, scale=1)
        plt.axis('image')
        plt.title("velocity")
        divider2 = make_axes_locatable(ax[3])
        cax3 = divider2.append_axes('right', size='5%', pad=0.05)
        fig.colorbar(sp[3],cax=cax3)

        plt.tight_layout()
            
    else:        
        #Update plots
        fig.sca(ax[0])
        sp[0].set_data(eta)

        fig.sca(ax[1])
        sp[1].set_data(hu)
        
        fig.sca(ax[2])
        sp[2].set_data(hv)

        fig.sca(ax[3])
        sp[3].set_data(velocity)
        quiv.set_UVC(qu, qv)
    
    return ax, sp, quiv


def ncAnimation(filename, nctype, **kwargs):
    #Create figure and plot initial conditions
    fig = plt.figure(figsize=(20, 6))

    ncfile = Dataset(filename)

    red_grav_mode = False

    if nctype == "ROMS":
        t = ncfile.variables['ocean_time'][:]

        H_m = np.ma.array(ncfile["h"][1:-1,1:-1], mask=[1-ncfile["mask_rho"][1:-1,1:-1]])

        eta = np.ma.array(ncfile["zeta"][:,1:-1,1:-1], mask=len(t)*[1-ncfile["mask_rho"][1:-1,1:-1]])
        try:
            u = np.ma.array( 0.5*(ncfile["ubar"][:,1:-1,1:]+ncfile["ubar"][:,1:-1,:-1]), mask=len(t)*[1-ncfile["mask_rho"][1:-1,1:-1]])
            v = np.ma.array( 0.5*(ncfile["vbar"][:,1:,1:-1]+ncfile["vbar"][:,:-1,1:-1]), mask=len(t)*[1-ncfile["mask_rho"][1:-1,1:-1]])

            hu = u*H_m
            hv = v*H_m
        except:
            u = 0.5*(ncfile["u"][:,:,1:-1,1:]+ncfile["u"][:,:,1:-1,:-1])
            v = 0.5*(ncfile["v"][:,:,1:,1:-1]+ncfile["v"][:,:,:-1,1:-1])
            
            integrator = NetCDFInitialization.MLD_integrator(source_url, H_m, x0=1, x1=-1, y0=1, y1=-1)
            hu = np.ma.array(np.sum(integrator * u, axis=1), mask=len(t)*[1-ncfile["mask_rho"][1:-1,1:-1]])
            hv = np.ma.array(np.sum(integrator * v, axis=1), mask=len(t)*[1-ncfile["mask_rho"][1:-1,1:-1]])


    elif nctype == "gpuocean":
        t = ncfile["time"][:]

        eta = ncfile["eta"][:]
        hu  = ncfile["hu"][:]
        hv  = ncfile["hv"][:]

        H_m = ncfile["Hm"][:]

    elif nctype == "gpuocean-reduced_grav":
        t = ncfile["time"][:]

        eta = ncfile["eta"]
        hu  = ncfile["hu"][:]
        hv  = ncfile["hv"][:]

        H_m = ncfile["Hm"][:]
        
        red_grav_mode = True

        

    movie_frames = len(t)

    dx = 50
    dy = 50
    
    ax, sp, quiv = plotSolution(fig, 
                            eta[0],
                            hu[0],
                            hv[0],
                            H_m,
                            dx, dy, 
                            t[0], 
                            red_grav_mode,
                            **kwargs)


    #Helper function which simulates and plots the solution    
    def animate(i):
        t_now = t[0] + (i / (movie_frames-1)) * (t[-1] - t[0]) 

        k = np.searchsorted(t, t_now)
        if (k >= eta.shape[0]):
            k = eta.shape[0] - 1
        j = max(0, k-1)
        if (j == k):
            k += 1
        s = (t_now - t[j]) / (t[k] - t[j])

        plotSolution(fig, 
                        ((1-s)*eta[j] + s*eta[k]), 
                        ((1-s)*hu[j]  + s*hu[k]), 
                        ((1-s)*hv[j]  + s*hv[k]), 
                        (H_m+(1-s)*eta[j] + s*eta[k]), 
                        dx, dy, 
                        t_now, 
                        red_grav_mode,
                        **kwargs, ax=ax, sp=sp, quiv=quiv)

        clear_output(wait = True)
        #print(progress.getPrintString(i / (movie_frames-1)))

    #Matplotlib for creating an animation
    anim = animation.FuncAnimation(fig, animate, range(movie_frames), interval=250)
    plt.close(fig)
    
    return anim


## Generating GPUOcean Simulation

In [12]:
nx, ny = 250, 250
dx, dy = 50, 50
dt = 0.0

eta0 = 10*np.ones((ny+4,nx+4))
hu0  = np.zeros((ny+4,nx+4))
hv0  = np.zeros((ny+4,nx+4))
H    = 10*np.ones((ny+5,nx+5))

g = 0.01
f = 0.0 #1.2e-4
r = 0.0

In [13]:
from gpuocean.utils import WindStress
wind_stress = WindStress.WindStress(t=[0],X=[np.array([[0.0000]], dtype=np.float32)],Y=[np.array([[0.0001]], dtype=np.float32)])

In [14]:
from gpuocean.SWEsimulators import CDKLM16
sim = CDKLM16.CDKLM16(gpu_ctx, eta0, hu0, hv0, H, nx, ny, dx, dy, dt, g, f, r, wind_stress=wind_stress, write_netcdf=True)

Closing file /home/florianb/havvarsel/reduced-gravity-ocean-model/notebooks/netcdf_2022_12_02/CDKLM16_2022_12_02-17_39_07.nc ...


In [15]:
for i in range(96):
    sim.step(1800, write_now=True)

In [16]:
ncAnimation(sim.sim_writer.output_file_name, "gpuocean-reduced_grav")